In [2]:
from keras.datasets import mnist
from keras.models import Model, Sequential
from keras.layers import *
from keras.optimizers import Adam
from tqdm import tqdm
from keras.layers.advanced_activations import LeakyReLU
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import h5py

Using TensorFlow backend.


In [3]:
(X_train, Y_train), (X_test, Y_test) = mnist.load_data()


In [4]:
X_train = X_train.reshape(X_train.shape[0], 28, 28, 1)
X_test = X_test.reshape(X_test.shape[0], 28, 28, 1)

X_train = X_train.astype('float32')

# Scaling the range of the image to [-1, 1]
# Because we are using tanh as the activation function in the last layer of the generator
# and tanh restricts the weights in the range [-1, 1]
X_train = (X_train - 127.5) / 127.5

X_train.shape

(60000, 28, 28, 1)

In [5]:
generator = Sequential()
generator.add(Dense(1024, input_shape = (100,)))
generator.add(Activation('tanh'))
generator.add(Dense(128*7*7))
generator.add(BatchNormalization())
generator.add(Activation('tanh'))
generator.add(Reshape((7, 7, 128), input_shape=(128*7*7,)))
generator.add(UpSampling2D(size=(2, 2)))
generator.add(Conv2D(64, (5, 5), padding='same'))
generator.add(Activation('tanh'))
generator.add(UpSampling2D(size=(2, 2)))
generator.add(Conv2D(1, (5, 5), padding='same'))
generator.add(Activation('tanh'))

In [6]:
generator.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 1024)              103424    
_________________________________________________________________
activation_1 (Activation)    (None, 1024)              0         
_________________________________________________________________
dense_2 (Dense)              (None, 6272)              6428800   
_________________________________________________________________
batch_normalization_1 (Batch (None, 6272)              25088     
_________________________________________________________________
activation_2 (Activation)    (None, 6272)              0         
_________________________________________________________________
reshape_1 (Reshape)          (None, 7, 7, 128)         0         
_________________________________________________________________
up_sampling2d_1 (UpSampling2 (None, 14, 14, 128)       0         
__________

In [7]:
discriminator = Sequential()
discriminator.add(Conv2D(64, (5, 5),input_shape=(28, 28, 1) , strides = (2,2)))
discriminator.add(BatchNormalization())
discriminator.add(Activation('tanh'))
discriminator.add(Conv2D(128, (5, 5) , strides = (2,2)))
discriminator.add(BatchNormalization())
discriminator.add(Activation('tanh'))
discriminator.add(Flatten())
discriminator.add(Dense(1024))
discriminator.add(Activation('relu'))
discriminator.add(Dense(1))
discriminator.add(Activation('sigmoid'))

In [8]:
generator.compile(loss = 'binary_crossentropy' , optimizer = 'adam')
discriminator.compile(loss = 'binary_crossentropy' , optimizer = 'adam')

In [9]:
discriminator.trainable = False
ganInput = Input(shape=(100,))
# getting the output of the generator
# and then feeding it to the discriminator
# new model = D(G(input))
x = generator(ganInput)
ganOutput = discriminator(x)
gan = Model(inputs=ganInput, outputs=ganOutput)
gan.compile(loss='binary_crossentropy', optimizer=Adam())

In [15]:
def train(epoch=10, batch_size=128):
    batch_count = X_train.shape[0] // batch_size
    
    for i in range(epoch):
        for j in tqdm(range(batch_count)):
            # Input for the generator
            noise_input = np.random.rand(batch_size, 100)
            
            # getting random images from X_train of size=batch_size 
            # these are the real images that will be fed to the discriminator
            image_batch = X_train[np.random.randint(0, X_train.shape[0], size=batch_size)]
            
            # these are the predicted images from the generator
            predictions = generator.predict(noise_input, batch_size=batch_size)
                        
            # the discriminator takes in the real images and the generated images
            X = np.concatenate([predictions, image_batch])
            
            # labels for the discriminator
            y_discriminator = [0]*batch_size + [1]*batch_size
            
            # Let's train the discriminator
            discriminator.trainable = True
            discriminator.fit(X, y_discriminator , verbose = 1)
            
            # Let's train the generator
            noise_input = np.random.rand(batch_size, 100)
            y_generator = [1]*batch_size
            discriminator.trainable = False
            gan.fit(noise_input, y_generator , verbose = 1)

In [ ]:
train(300, 128)



  0%|          | 0/468 [00:00<?, ?it/s]

Epoch 1/10
256/256 [==============================] - 0s - loss: 0.1601     
Epoch 2/10
256/256 [==============================] - 0s - loss: 0.1663     
Epoch 3/10
256/256 [==============================] - 0s - loss: 0.1549     
Epoch 4/10
256/256 [==============================] - 0s - loss: 0.0623         
Epoch 5/10
256/256 [==============================] - 0s - loss: 0.0625     
Epoch 6/10
256/256 [==============================] - 0s - loss: 0.0205     
Epoch 7/10
256/256 [==============================] - 0s - loss: 5.3703e-04     
Epoch 8/10
256/256 [==============================] - 0s - loss: 6.3054e-04     
Epoch 9/10


256/256 [==============================] - 0s - loss: 9.5014e-05     
Epoch 10/10
256/256 [==============================] - 0s - loss: 7.8227e-05     
Epoch 1/1
128/128 [==============================] - 2s - loss: 10.9998     

  0%|          | 1/468 [00:10<1:21:44, 10.50s/it]


Epoch 1/10
256/256 [==============================] - 1s - loss: 0.1532     
Epoch 2/10
256/256 [==============================] - 1s - loss: 0.0174     
Epoch 3/10
256/256 [==============================] - 1s - loss: 0.0159     
Epoch 4/10
256/256 [==============================] - 1s - loss: 0.0015         
Epoch 5/10
256/256 [==============================] - 1s - loss: 0.0037     
Epoch 6/10
256/256 [==============================] - 1s - loss: 3.6562e-04     
Epoch 7/10
256/256 [==============================] - 1s - loss: 2.5153e-04     
Epoch 8/10
256/256 [==============================] - 0s - loss: 0.0032     
Epoch 9/10
256/256 [==============================] - 0s - loss: 5.9420e-04     A: 0s - loss: 
Epoch 10/10
256/256 [==============================] - 0s - loss: 4.9671e-04     
Epoch 1/1
128/128 [==============================] - 2s - loss: 10.3242     

...


Epoch 1/10
256/256 [==============================] - 0s - loss: 0.0630     
Epoch 2/10
256/256 [==============================] - 0s - loss: 0.0630     
Epoch 3/10
256/256 [==============================] - 0s - loss: 0.0630     
Epoch 4/10
256/256 [==============================] - 0s - loss: 0.0630         
Epoch 5/10
256/256 [==============================] - 0s - loss: 0.0630        
Epoch 6/10
256/256 [==============================] - 0s - loss: 0.0630     
Epoch 7/10
256/256 [==============================] - 0s - loss: 0.0630     
Epoch 8/10
256/256 [==============================] - 0s - loss: 0.0630        
Epoch 9/10
256/256 [==============================] - 0s - loss: 0.0630      
Epoch 10/10
256/256 [==============================] - 0s - loss: 0.0630       
Epoch 1/1
128/128 [==============================] - 2s - loss: 9.7777     

 51%|█████     | 239/468 [41:25<39:01, 10.22s/it]


Epoch 1/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 2/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 3/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 4/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 5/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 6/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 7/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 8/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 9/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 10/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 1/1
128/128 [==============================] - 2s - loss: 10.1567     

 51%|█████▏    | 240/468 [41:36<38:57, 10.25s/it]


Epoch 1/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 2/10
256/256 [==============================] - 0s - loss: 1.0960e-07     
Epoch 3/10
192/256 [=====================>........] - ETA: 0s - loss: 0.0830   

In [ ]:
generator.save_model('gen.h5')
discriminator.save_model('dis.h5')